# Interpolation

- Assume, we have a function $y(x)$ that is sampled at $n$ discrete points ${x_1, x_2, \cdots, x_n}$ with high accuracy
    - This data could be obtained from experiments or simulations (e.g., FDM, FEM)

- How to evaluate $y(x^*)$ where $x_i < x^* < x_j$ ($1\le i \lt j\le n$)?
    - Use _interpolation_

<img src="../images/interpolation.png" width=720>

- Interpolation is the process of contructing a function $\hat{y}(x)$ that is exact at the sampled points and approximates the function elsewhere
    - $\hat{y}(x)$ is the interpolation function

## Interpolation Types

- Piecewise constant
- Linear
- Quadratic
- Cubic spline
- Higher-order splines
- ...

Piecewise constant interpolation of data sampled from $sin(x)$

<img src="../images/interpolation_types1.png" width=720>

Linear interpolation of data sampled from $sin(x)$

<img src="../images/interpolation_types2.png" width=720>

Cubic interpolation of data sampled from $sin(x)$

<img src="../images/interpolation_types_cubic.png" width=720>

- _Key assumption:_ input data has adequate information to construct an interpolation function that is sufficiently accurate
    - Fewer samples $\implies$ poor interpolation

Interpolation with four samples (left) and three samples (right)

<img src="../images/few_samples_poor_interpolation.png" width=1440>

- The _scipy_ sub-module `interpolate` provides classes for interpolation
    - Univariate interpolation (1D data)
        - `interp1d`
        - `InterpolatedUnivariateSpline`
        - $\cdots$
    - Multivariate interpolation
        - 2D data
            - `interp2d`
            - `BivariateSpline` and derived classes
            - $\cdots$
        - $n$D data
            - `interpn`

- Refer to [documentation](https://docs.scipy.org/doc/scipy/reference/interpolate.html) for more details

### Example

- Find an interpolation function for sampled data from $sin(x)$

In [ ]:

%matplotlib widget
import numpy as np
from scipy import interpolate
import matplotlib.pyplot as plt

# Sampled data from sin
xs = np.linspace(0, 2*np.pi, 8)
ys = np.sin(xs)


In [ ]:

# Cubic spline interpolation
f1 = interpolate.interp1d(xs, ys, kind = 'cubic')

# Alternate approach
f2 = interpolate.InterpolatedUnivariateSpline(xs, ys, k = 3)


- `f1` and `f2` are both _callable_ objects and can be treated as any other Python function

- Using the interpolation function beyond the bounds of the sampled data will cause an error

In [ ]:

# Interpolated data
x = np.linspace(0, 2*np.pi, 100)
y1 = f1(x)
y2 = f2(x)


In [ ]:

# Plot
fig, axs = plt.subplots(2, 1)
axs[0].plot(x, y1, '-r', label='interp1d')
axs[1].plot(x, y2, '-r', label='UnivariateSpline')
for ax in axs:
    ax.plot(xs, ys, 'ok', markersize=6, label='Samples')
    ax.plot(x, np.sin(x), '--b', label='sin(x)')
    ax.legend();


## Curve Fitting

- Given noisy data, what is the best mathematical model (i.e., function) that fits the data?

<img src="../images/curve_fitting.png" width=720>

- Least squares fitting, or _regression_, is a common approach
    - Minimizes the squared error in the predicted values of the best fit $\hat{y}$ and the actual values $y$

$$
E = \sum\limits_{i=0}^n \left( \hat{y}(x_i) - y(x_i) \right)^2 
$$

- The unknown model can be written as:

$$ \hat{y} = f(x, a_0, a_1, \cdots, a_j) $$

- Here, $f$ is a known function with $a_0, a_1, \cdots, a_j$ being unknown coefficients to be determined by minimizing the error $E$

- If the mathematical model $f$ is a polynomial, it is referred to as _linear regression_

- Curve fitting in _numpy_ and _scipy_
    - `np.linalg.lstsq`
        - Works for mathematical models of the form: $ \hat{y}(x) = \sum\limits_{i=0}^n a_i f_i(x)$
        - Minimizing the error in this case is equivalent to solving a linear system with $a_i$ being the unknowns

- Fitting with polynomial functions
    - `np.polynomial` subpackage provides modules for working special polynomial functions like
        - Polynomial
        - Chebyshev
        - Lagrange
        - Legendre
        - Laguerre
        - $\cdots$

- Fitting with splines
    - `scipy.interpolate.UnivariateSpline` class

- Fitting with `scipy.optimize`
    - `optimize.curve_fit` which internally uses `optimize.least_squares`
    - Allows non-linear least squares fit

### Example

- Fit data sampled from $sin$ with added noise

In [ ]:

# Seed for random numbers
np.random.seed(2412023)

# Data with noise - typically obtained from experiments
x = np.linspace(0, 2*np.pi, 200)
y = np.sin(x) + 0.25*np.random.rand(len(x))


- Curve fitting with the model $\hat{y}(x) = a_0 + a_1 sin(x) + a_2 cos(x)$

- For an arbitrary point $x_i$ with a function value of $y_i$, we have:

$$ y_i = a_0 + a_1 sin(x_i) + a_2 cos(x_i) $$

- This gives us $n$ equations in $a_0, a_1$, and $a_2$ ($n$ = number of samples)

In [ ]:

# Least squares fit
A = np.vstack([np.ones_like(x),
               np.sin(x),
               np.cos(x)]).T
fit = np.linalg.lstsq(A, y)
fit[0] # ignore the warning


In [ ]:

# Fitted curve
y_fit = fit[0][0] + fit[0][1]*np.sin(x) + fit[0][2]*np.cos(x)

# Plot
def plot_fit(x_fit, y_fit, lbl='Fit'):
    fig, ax = plt.subplots()
    ax.plot(x, y, 'ok', markersize=2, label="Samples")
    ax.plot(x_fit, y_fit, '-r', label=lbl)
    ax.set(xlabel='x', ylabel='y')
    ax.legend();

plot_fit(x, y_fit, "Least Squares Fit")

- Fit with a 6<sup>th</sup> degree polynomial

In [ ]:

# Least squares polynomial fit of order 6
fitPoly = np.polynomial.Polynomial.fit(x, y, 6)
print(fitPoly)


In [ ]:

# Plot
x_fit, y_fit = fitPoly.linspace()
plot_fit(x_fit, y_fit, "Polynomial Fit")


- Fit with a 6<sup>th</sup> degree Laguerre polynomials

In [ ]:

# Least squares Laguerre polynomial fit of order 6
fitLaguerre = np.polynomial.Laguerre.fit(x, y, 6)
print(fitLaguerre)


In [ ]:

# Plot
x_fit, y_fit = fitLaguerre.linspace()
plot_fit(x_fit, y_fit, "Laguerre Poly Fit")


- Fit with a spline function

In [ ]:

# Spline fitting
fitSpline = interpolate.UnivariateSpline(x, y)

# Interpolation function
yHat = fitSpline(x)

# Plot
plot_fit(x, yHat, "Spline fit")


- Fitting using the `optimize` sub-module
    - Needs a prescribed mathematical model
    
$$ \hat{y}(x) = a_0 + a_1 sin(k_1 x) + a_2 cos(k_2 x) $$

- Unlike the `linalg.lstsq` function, the model can be _non-linear_

In [ ]:

from scipy import optimize

# Model function - can be non-linear
def model_func(x, a0, a1, k1, a2, k2):
    return a0 + a1*np.sin(k1*x) + a2*np.cos(k2*x)

# Fit
optPar, covPar = optimize.curve_fit(model_func, x, y)
optPar # Optimized parameters


In [ ]:

# Plot
y_fit = model_func(x, optPar[0], optPar[1], optPar[2], optPar[3], optPar[4])
plot_fit(x, y_fit, "Nonlinear least squares fit")


## References

- Interpolation
    - https://pythonnumericalmethods.berkeley.edu/notebooks/chapter17.00-Interpolation.html
- Regression/curve fitting
    - https://pythonnumericalmethods.berkeley.edu/notebooks/chapter16.00-Least-Squares-Regression.html